# Acute Coronary Syndrome Study

Lets see if we can run [the queries](http://build.fhir.org/ig/HL7/vulcan-rwd/acs.html) for cohort criteria.

See:
- https://clinicaltrials.gov/ct2/show/NCT02190123
- https://confluence.hl7.org/display/FHIR/Public+Test+Servers
- [postman workspace](https://vulcan-rwd-ig.postman.co/workspace/vulcan_rwd_ig~0893112e-5070-4e47-9dc0-0c60dd59caf2)

The endpoint is: https://fhir.6eyq21exgcnv.workload-nonprod-fhiraas.isccloud.io
Key is: DopIqILDrN79nglZYvGPz2bP1XfeIqMq8Vb9dRsP

In [ ]:
import requests, json, datetime

# Define a simple client that can talk to FHIR servers

In [ ]:
class FhirClient:
    def __init__(self, api_base, x_api_key=None):
        self.api_base = api_base
        self.request_headers = {}
        if x_api_key is not None:
            self.request_headers['x-api-key'] = x_api_key
    
    def get_as_response(self, resource_type, id_or_params=None):
        "GET FHIR resources of `resource_type` and return python `reponse`"
        url = f'{self.api_base}/{resource_type}'
#         params = dict(_format = 'json') 
        params = {} # $retrieveExtendedIPS] with parameters [[_format]] doesn't work on ips.health/fhir
        if isinstance(id_or_params, dict): 
            params = {**params, **id_or_params}
        elif isinstance(id_or_params, str): # TODO: drop str param support
            if id_or_params[0] in ['/','?']: raise Exception(f'invalid id_or_params {id_or_params}') # TODO: clean
            url += f'/{id_or_params}'
        response = requests.get(url, params, headers=self.request_headers)
        print('GET', response.url)
        return response
    
    def get_as_raw_json(self, resource_type, id_or_params=None):
        "GET FHIR resources of `resource_type` in JSON format"
        return self.get_as_response(resource_type, id_or_params).json()
    
    def get_next_as_raw_json(self, json_response):
        "GET the next set of results"
        for link in json_response['link']:
            if link['relation'] == 'next':
                url = link['url']
                print('GET',url)
                return requests.get(url, headers=self.request_headers).json()

    def get_by_reference(self, reference):
        "Return a resource read from a FHIR server by reference, as a list containg a single bundle entry"
        if reference.startswith(self.api_base):
            reference = reference[len(self.api_base):].strip('/')
        if reference.startswith('http'):
            print(f'WARNING: Found reference {reference} that does not start with {api_base}')
            return []
        resource_type, id = reference.split('/')
        single_resource = self.get_as_raw_json(resource_type, id)
        return [dict(fullUrl = f'{self.api_base}/{resource_type}/{id}', resource = single_resource)]

## Quick client test/demo

In [ ]:
# client = FhirClient('https://server.fire.ly/r4')
# client.get_as_raw_json('Patient', dict(birthdate='le2002-09-01', gender='male,female'))

# Define some helper functions

In [ ]:
def extract_references_from_resource(resource, field_name):
    "Return a list of references extracted from a single resource and field"
    result = []
    if field_name in resource:
        references = resource[field_name]
        if not isinstance(references, list): references = [references]
        for reference in references:
            _reference = reference.get('reference')
            if _reference is None: continue
            if _reference.startswith('#'): continue
            # TODO: check that we have a relative reference or handle other kinds too
            result.append(_reference)
    return result

In [ ]:
with open('test/data/Patient_bundle.json') as f:
    _patient_bundle = json.load(f)
with open('test/data/MedicationAdministration_bundle.json') as f:
    _medication_administration_bundle = json.load(f)

In [ ]:
extract_references_from_resource(_medication_administration_bundle['entry'][0]['resource'], 'subject')

['Patient/1ac8947d-038f-4cc7-81fa-a32e694187e8']

In [ ]:
# #export
# def extract_references(bundle, field_names):
#     "Return a list of relative references e.g. `['Condition/1ddef4ad-fb76-46d6-9f1d-8ed58b173ee8']`"
#     if 'entry' not in bundle: return []
#     result = []
#     for entry in bundle['entry']:
#         resource = entry.get('resource', {})
#         for f in field_names:
#             result.extend(extract_references_from_resource(resource, f))
#     return list(set(result)) # de-duplicate but still return a list

In [ ]:
def pull_attr(resouce, attr_path):
    "Pull a value from `resource` if we can find the attribute specified"
    for _attr_path in attr_path.split(' OR '):
        r, found = resouce, True
        for _attr in _attr_path.split('.'):
            if not _attr in r:
                found = False
                break
            r = r[_attr]
            if isinstance(r, list) and r:
                r = r[0] # TODO: is it OK to just pull the 1st item from the list?
        if found:
            return r

In [ ]:
_medication_administration_bundle['entry'][0]['resource']

{'resourceType': 'MedicationAdministration',
 'id': '578233',
 'meta': {'versionId': '1', 'lastUpdated': '2020-10-05T22:51:23.402-04:00'},
 'status': 'completed',
 'medicationCodeableConcept': {'coding': [{'system': 'http://www.nlm.nih.gov/research/umls/rxnorm',
    'code': '1734340',
    'display': 'Etoposide 100 MG Injection'}],
  'text': 'Etoposide 100 MG Injection'},
 'subject': {'reference': 'Patient/1ac8947d-038f-4cc7-81fa-a32e694187e8'},
 'context': {'reference': 'Encounter/578179'},
 'effectiveDateTime': '1970-09-24T17:14:01-04:00',
 'reasonReference': [{'reference': 'Condition/576320'}]}

In [ ]:
pull_attr(_medication_administration_bundle['entry'][0]['resource'], 'medicationCodeableConcept.coding.display')

'Etoposide 100 MG Injection'

In [ ]:
def extract_patient_ids(bundle):
    "Return a list relative references of all patients found in a bundle"
    # Note: no checks are made that the bundle contains resources of the same type etc
    if 'entry' not in bundle:
        return []
    result = []
    for entry in bundle['entry']:
        resource = entry['resource']
        if resource['resourceType'] == 'OperationOutcome':
            continue # e.g. "Unrecognized parameter 'dischargeDisposition'. exp"
        if resource['resourceType'] == 'Patient':
            result.append('Patient/' + resource['id'])
        else:
            result.append(resource['subject']['reference'])
    return result

In [ ]:
extract_patient_ids(_medication_administration_bundle)[:3]

['Patient/1ac8947d-038f-4cc7-81fa-a32e694187e8',
 'Patient/576285',
 'Patient/576285']

## If we need to run multiple queries ...

... to implement inclusion criteria, we'll need an intersection of patients returned

In [ ]:
def intersection_patient_ids(*bundles):
    "Returns a list of references for all patients found in all bundles"
    all_patient_ids = []
    for bundle in bundles:
        all_patient_ids.append(extract_patient_ids(bundle))
    all_patient_ids = [set(ids) for ids in all_patient_ids]
    result = all_patient_ids[0]
    for ids in all_patient_ids[1:]:
        result = result & ids
    return list(result)

In [ ]:
(
    len(intersection_patient_ids(_patient_bundle, _medication_administration_bundle)),
    len(intersection_patient_ids(_patient_bundle)), 
    len(intersection_patient_ids(_medication_administration_bundle))
)

(1, 50, 12)

In [ ]:
# medication_administration_bundle['entry'][0]['resource']

In [ ]:
def extract_resources_by_patient_id(bundle, patient_reference):
    "Return a list of resources pulled from `bundle` that belong to `patient_reference`"
    if 'entry' not in bundle:
        return []
    result = []
    for entry in bundle['entry']:
        resource = entry['resource']
        if resource['resourceType'] == 'OperationOutcome':
            continue # e.g. "Unrecognized parameter 'dischargeDisposition'. exp"
        if resource['resourceType'] == 'Patient':
            if resource['id'] == patient_reference.split('/')[1]:
                result.append(resource)
        else:
            if resource['subject']['reference'] == patient_reference:
                result.append(resource)
    return result

# Run a few test queries against a FHIR server to see what we can use

In [ ]:
def check_data(api_base, x_api_key=None):
    client = FhirClient(api_base, x_api_key)
    def _call_and_check(resource_type, id_or_params=None):
        response = client.get_as_response(resource_type, id_or_params)
        print(response)
        try:
            json_response = response.json()
        except:
            json_response = None
            print('ERROR: expected JSON response but found\n', response.text[:100])
        if json_response is not None:
            if response.status_code != 200:
                print(json_response)
            else:
                if 'total' in json_response:
                    print('Total', json_response['total'])
                elif 'entry' in json_response:
                    print('Total', len(json_response['entry']), 'derived from "entry"')
                else:
                    print('TODO: failed to find total')
                    print(json_response)
        print('')
    _call_and_check('Patient', dict(birthdate='le2002-09-01', gender='male,female'))
    _call_and_check('Patient', {'birthdate': 'le2002-09-01', 'gender:missing': 'false'})
    _call_and_check('Patient/1234/$retrieveExtendedIPS')
    _call_and_check('Patient/1234/$summary')
    _call_and_check('Encounter', {
        'reason-code:below': 'I20,I21,I22,I23,I24,I25',
        'date': 'ge2000-09-01&date=le2021-09-30', # TODO: clean this up
#         'date': 'le2021-09-30', # Sep has no 31 (o: - might want an IG update
        'status': 'finished',
        'dischargeDisposition:not':'exp'})
    _call_and_check('Encounter', {
        'reason-code': 'I20,I21,I22,I23,I24,I25', # take out :below
        'date': 'ge2000-09-01&date=le2021-09-30',
#         'date': 'le2021-09-30',
        'status': 'finished'})
    _call_and_check('MedicationAdministration', {
        'status': 'completed',
#         'effective-time': 'ge[Encounter-Start-Date]',
        'code': 'http://www.nlm.nih.gov/research/umls/rxnorm|1116632,'
                'http://www.nlm.nih.gov/research/umls/rxnorm|613391,'
                'http://www.nlm.nih.gov/research/umls/rxnorm|32968,'
                'http://www.nlm.nih.gov/research/umls/rxnorm|687667,'
                'http://www.nlm.nih.gov/research/umls/rxnorm|153658'})

## intersystems prod

In [ ]:
check_data('https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io', 'cqUrrk3NQd8BJPJoUD4Qz6tpjADJ0W1w10dPNARd')

GET https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/Patient?birthdate=le2002-09-01&gender=male%2Cfemale
<Response [200]>
Total 1155

GET https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/Patient?birthdate=le2002-09-01&gender%3Amissing=false
<Response [400]>
{'resourceType': 'OperationOutcome', 'issue': [{'severity': 'error', 'code': 'not-supported', 'diagnostics': '<HSFHIRErr>UnsupportedParameterModifier', 'details': {'text': "Unsupported modifier 'missing' on param 'gender"}}]}

GET https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/Patient/1234/$retrieveExtendedIPS
<Response [400]>
{'resourceType': 'OperationOutcome', 'issue': [{'severity': 'error', 'code': 'invalid', 'diagnostics': '<HSFHIRErr>InvalidOperationName', 'details': {'text': "The operation name 'retrieveExtendedIPS' is not valid."}}]}

GET https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/Patient/1234/$summary
<Response [400]>
{'resourceType': 'OperationOutcome', 'issue': [{'severi

In [ ]:
client = FhirClient('https://ips.health/fhir')
client.get_as_raw_json('Patient')

GET https://ips.health/fhir/Patient


{'resourceType': 'Bundle',
 'id': '9c8367cd-997e-4b66-9fc6-3910938931fc',
 'meta': {'lastUpdated': '2022-09-18T17:40:14.276+00:00'},
 'type': 'searchset',
 'total': 137,
 'link': [{'relation': 'self', 'url': 'https://ips.health/fhir/Patient'},
  {'relation': 'next',
   'url': 'https://ips.health/fhir?_getpages=9c8367cd-997e-4b66-9fc6-3910938931fc&_getpagesoffset=20&_count=20&_pretty=true&_bundletype=searchset'}],
 'entry': [{'fullUrl': 'https://ips.health/fhir/Patient/1',
   'resource': {'resourceType': 'Patient',
    'id': '1',
    'meta': {'versionId': '1',
     'lastUpdated': '2022-09-06T21:12:47.040+00:00',
     'source': '#fUPtWa97RV5lOt2l'},
    'text': {'status': 'generated',
     'div': '<div xmlns="http://www.w3.org/1999/xhtml"><p><b>Generated Narrative</b></p><div style="display: inline-block; background-color: #d9e0e7; padding: 6px; margin: 4px; border: 1px solid #8da1b4; border-radius: 5px; line-height: 60%"><p style="margin-bottom: 0px">Resource &quot;2b90dd2b-2dab-4c75-9b

In [ ]:
check_data('https://ips.health/fhir')

GET https://ips.health/fhir/Patient?birthdate=le2002-09-01&gender=male%2Cfemale
<Response [200]>
Total 125

GET https://ips.health/fhir/Patient/1234/$retrieveExtendedIPS
<Response [400]>
{'resourceType': 'OperationOutcome', 'text': {'status': 'generated', 'div': '<div xmlns="http://www.w3.org/1999/xhtml"><h1>Operation Outcome</h1><table border="0"><tr><td style="font-weight: bold;">ERROR</td><td>[]</td><td><pre>Invalid request: The FHIR endpoint on this server does not know how to handle GET operation[Patient/1234/$retrieveExtendedIPS] with parameters [[]]</pre></td>\n\t\t\t</tr>\n\t\t</table>\n\t</div>'}, 'issue': [{'severity': 'error', 'code': 'not-supported', 'diagnostics': 'Invalid request: The FHIR endpoint on this server does not know how to handle GET operation[Patient/1234/$retrieveExtendedIPS] with parameters [[]]'}]}

GET https://ips.health/fhir/Patient/1234/$summary
<Response [500]>
{'resourceType': 'OperationOutcome', 'text': {'status': 'generated', 'div': '<div xmlns="http

## intersystems dev

In [ ]:
# check_data('https://fhir.6eyq21exgcnv.workload-nonprod-fhiraas.isccloud.io', 'DopIqILDrN79nglZYvGPz2bP1XfeIqMq8Vb9dRsP')

## and a few others ...

In [ ]:
# check_data('https://server.fire.ly/r4')

In [ ]:
# check_data('https://r4.smarthealthit.org/')

In [ ]:
# check_data('http://test.fhir.org/r4')

In [ ]:
# check_data('http://hapi.fhir.org/baseR4')

In [ ]:
# check_data('https://spark.incendi.no')

In [ ]:
# check_data('http://sandbox.hspconsortium.org')

The patients for this study would have the following criteria:
- female or male aged 18 years or older
- have a Encounter record representing a hospitalization with an initial diagnosis of Acute Coronary Syndrome where the patient was discharged alive some time between September 2020 to September 2021 :
    - ACS is represented for this scenario one of these ICD 10 codes (I21 Acute myocardial infarction; I20-I25 Ischemic heart diseases; I24 Other acute ischemic heart diseases)
    - the Encounter diagnosis will point to a Condition with one of those codes
    - the Encounter will have hospitalization information included
    - the Encounter hospitalization discharge disposition code is not ‘exp’ (expired)
- have been given one of ticagrelor, prasugrel or clopidogrel after the date of diagnosis of ACS (as represented by the Condition or Encounter record found above)

| Drug Name    | Brand Name  | RxNorm CUI            |
|--------------|-------------|-----------------------|
| ticagrelor   | brilinta    | 1116632               |
| prasurgrel   | effient     | 613391                |
| clopidogrel  | plavix      | 32968, 687667, 153658 |

These criteria would be represented by the following queries:

```
/Patient?birthdate=le2002-09-01&gender=male,female

/Encounter?reason-code:below=I20,I21,I22,I23,I24,I25&date=ge2020-09-01&date=le2021-09-31&status=finished&dischargeDisposition:not=exp

/MedicationAdministration?status=completed&effective-time=ge[Encounter-Start-Date]&
  code=http://www.nlm.nih.gov/research/umls/rxnorm|1116632,http://www.nlm.nih.gov/research/umls/rxnorm|613391,http://www.nlm.nih.gov/research/umls/rxnorm|32968,http://www.nlm.nih.gov/research/umls/rxnorm|687667,http://www.nlm.nih.gov/research/umls/rxnorm|153658
```

# Lets run the queries from the IG

# Patient

In [ ]:
# client = FhirClient('https://server.fire.ly/r4')
# client = FhirClient('https://r4.smarthealthit.org/')
# client = FhirClient('https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io', 'cqUrrk3NQd8BJPJoUD4Qz6tpjADJ0W1w10dPNARd')
# client = FhirClient('https://fhir.6eyq21exgcnv.workload-nonprod-fhiraas.isccloud.io', 'DopIqILDrN79nglZYvGPz2bP1XfeIqMq8Vb9dRsP')
client = FhirClient('https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io')
patient_bundle = client.get_as_raw_json('Patient', dict(birthdate='le2002-09-01', gender='male,female'))
patient_bundle

GET https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/Patient?birthdate=le2002-09-01&gender=male%2Cfemale


{'resourceType': 'Bundle',
 'id': '6fe2acf6-377a-11ed-8cfe-02a7b1c59300',
 'type': 'searchset',
 'timestamp': '2022-09-18T17:41:01Z',
 'total': 1155,
 'link': [{'relation': 'first',
   'url': 'https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/Patient?page=1&queryId=47b79746-377a-11ed-8cfe-02a7b1c59300'},
  {'relation': 'self',
   'url': 'https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/Patient?birthdate=le2002-09-01&gender=male%2Cfemale'},
  {'relation': 'next',
   'url': 'https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/Patient?page=2&queryId=47b79746-377a-11ed-8cfe-02a7b1c59300'},
  {'relation': 'last',
   'url': 'https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/Patient?page=2&queryId=47b79746-377a-11ed-8cfe-02a7b1c59300'}],
 'entry': [{'fullUrl': 'https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/Patient/3254',
   'resource': {'resourceType': 'Patient',
    'id': '3254',
    'meta': {'profile': ['https://hl7.org/fhir/us/core/Struc

# Encounter

TODO: is there an efficient way to search for `Encounter`s that have hospitalization?
- maybe `dischargeDisposition=home,alt-home,other-hcf, ... ` would work if we can rely on conformance to value set

dischargeDisposition is unreliable and messy in real life - some systems won't allow collection of death - death records are handled separatly ...

for this study, we will not filter on dicharge - we could/should pull death records (or other evidence of patient still being alive)

In [ ]:
# client = FhirClient('https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io')
# client.get_as_raw_json('Encounter/1156769')

In [ ]:
encounter_bundle = client.get_as_raw_json('Encounter', {
        'reason-code': 'I20,I21,I22,I23,I24,I25', # TODO: not using below for now 'reason-code:below': 'I20,I21,I22,I23,I24,I25',
        'date': 'ge2000-09-01&date=le2021-09-30',
        'status': 'finished',
#         'dischargeDisposition:not':'exp' # TODO: Do this client side for now
})
encounter_bundle

GET https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/Encounter?reason-code=I20%2CI21%2CI22%2CI23%2CI24%2CI25&date=ge2000-09-01%26date%3Dle2021-09-30&status=finished


{'resourceType': 'Bundle',
 'id': '642d0bbe-3779-11ed-8cff-02a7b1c59300',
 'type': 'searchset',
 'timestamp': '2022-09-18T17:41:38Z',
 'total': 59,
 'link': [{'relation': 'self',
   'url': 'https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/Encounter?date=ge2000-09-01&date=le2021-09-30&reason-code=I20%2CI21%2CI22%2CI23%2CI24%2CI25&status=finished'}],
 'entry': [{'fullUrl': 'https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/Encounter/598736eb37a1668534e8fd4011235347',
   'resource': {'resourceType': 'Encounter',
    'id': '598736eb37a1668534e8fd4011235347',
    'identifier': [{'value': 'a76fe8757bac1e14d49e6dfebb9fbff7-Encounter'}],
    'status': 'finished',
    'class': {'system': 'https://hl7.org/fhir/v3/ActCode', 'code': 'IMP'},
    'subject': {'reference': 'Patient/1bbc2bc53ed277ac09507e6893743410'},
    'basedOn': [{'reference': 'ServiceRequest/5a4b033e3493640a72c8b87f8cb05106'}],
    'period': {'start': '2013-02-10', 'end': '2013-02-10'},
    'reasonCode': [{'co

none of these &uarr; have hospitalization ... so they should all be filtered out

but ... this also means no encounters have dischargeDisposition=exp &darr;

In [ ]:
for encounter in encounter_bundle['entry']:
    resource = encounter['resource']
    dischargeDisposition = pull_attr(resource, 'hospitalization.dischargeDisposition.coding.code')
    if dischargeDisposition is not None:
        print('resource might need to be filtered', dischargeDisposition) 
#     print(resource['id'], pull_attr(resource, 'hospitalization.dischargeDisposition.coding.code'), pull_attr(resource, 'reasonCode.coding.display'))

In [ ]:
# client.get_as_raw_json('Encounter/1156769')

In [ ]:
# bundle = client.get_as_raw_json('Encounter', {'status': 'finished'})
# bundle

In [ ]:
# page_count, page_limit = 0, 10000
# bundle = client.get_as_raw_json('Encounter', {'status': 'finished'})
# for encounter in bundle['entry']:
#     if encounter['resource']['id'] == '1156769':
#         raise Exception('found it')
# while bundle is not None:
#     page_count += 1
#     if page_count > page_limit:
#         print('Stopping early')
#         break
#     bundle = client.get_next_as_raw_json(bundle)
#     for encounter in bundle['entry']:
#         hospitalization = pull_attr(encounter, 'resource.hospitalization')
#         if hospitalization is not None:
#             print(pull_attr(encounter, 'fullUrl'), hospitalization)
#         if encounter['resource']['id'] == '1156769':
#             raise Exception('found it')

# Medication

In [ ]:
medication_administration_bundle = client.get_as_raw_json('MedicationAdministration', {
        'status': 'completed',
#         'effective-time': 'ge[Encounter-Start-Date]', # TODO: don't think this is possible via FHIR query
        'code': 'http://www.nlm.nih.gov/research/umls/rxnorm|1116632,'
                'http://www.nlm.nih.gov/research/umls/rxnorm|613391,'
                'http://www.nlm.nih.gov/research/umls/rxnorm|32968,'
                'http://www.nlm.nih.gov/research/umls/rxnorm|687667,'
                'http://www.nlm.nih.gov/research/umls/rxnorm|153658'})
medication_administration_bundle

GET https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/MedicationAdministration?status=completed&code=http%3A%2F%2Fwww.nlm.nih.gov%2Fresearch%2Fumls%2Frxnorm%7C1116632%2Chttp%3A%2F%2Fwww.nlm.nih.gov%2Fresearch%2Fumls%2Frxnorm%7C613391%2Chttp%3A%2F%2Fwww.nlm.nih.gov%2Fresearch%2Fumls%2Frxnorm%7C32968%2Chttp%3A%2F%2Fwww.nlm.nih.gov%2Fresearch%2Fumls%2Frxnorm%7C687667%2Chttp%3A%2F%2Fwww.nlm.nih.gov%2Fresearch%2Fumls%2Frxnorm%7C153658


{'resourceType': 'Bundle',
 'id': 'd79083e6-377a-11ed-8f77-02a7b1c59300',
 'type': 'searchset',
 'timestamp': '2022-09-18T17:41:44Z',
 'total': 1031,
 'link': [{'relation': 'first',
   'url': 'https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/MedicationAdministration?page=1&queryId=adaf1ede-377a-11ed-8f77-02a7b1c59300'},
  {'relation': 'self',
   'url': 'https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/MedicationAdministration?code=http%3A%2F%2Fwww.nlm.nih.gov%2Fresearch%2Fumls%2Frxnorm%7C1116632%2Chttp%3A%2F%2Fwww.nlm.nih.gov%2Fresearch%2Fumls%2Frxnorm%7C613391%2Chttp%3A%2F%2Fwww.nlm.nih.gov%2Fresearch%2Fumls%2Frxnorm%7C32968%2Chttp%3A%2F%2Fwww.nlm.nih.gov%2Fresearch%2Fumls%2Frxnorm%7C687667%2Chttp%3A%2F%2Fwww.nlm.nih.gov%2Fresearch%2Fumls%2Frxnorm%7C153658&status=completed'},
  {'relation': 'next',
   'url': 'https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/MedicationAdministration?page=2&queryId=adaf1ede-377a-11ed-8f77-02a7b1c59300'},
  {'relation': '

# How many patients can we find in all 3 bundles

In [ ]:
patient_ids = intersection_patient_ids(patient_bundle, encounter_bundle, medication_administration_bundle)
patient_ids

['Patient/e4c9f85f8b2b9a85b32f7d9a67ea1046',
 'Patient/00d7dde9ae58163184c3836f01deff61',
 'Patient/ceba63b6dcbda783668cf3efeea1d3dd',
 'Patient/f7f2e775f7ae3f7a095146cb4deaa497',
 'Patient/ff7c22942a1e16167f1b9c44f12aae05',
 'Patient/6863ac983b0b55455da78f1fdd1288ff']

In [ ]:
def get_encounter_date(encounter_bundle, patient_id):
    encounters = extract_resources_by_patient_id(encounter_bundle, patient_id)
    dates = []
    for encounter in encounters:
        dates.append(datetime.date.fromisoformat(pull_attr(encounter, 'period.start')))
    return min(dates)

In [ ]:
get_encounter_date(encounter_bundle, 'Patient/ff7c22942a1e16167f1b9c44f12aae05')

datetime.date(2014, 3, 26)

In [ ]:
patient_list = []
for patient_id in patient_ids:
    data = {
        'patient': extract_resources_by_patient_id(patient_bundle, patient_id)[0],
        'encounter': extract_resources_by_patient_id(encounter_bundle, patient_id)
    }
    patient_list.append(data)
    encounter_date = get_encounter_date(encounter_bundle, patient_id)
    print(patient_id, encounter_date)
    meds = extract_resources_by_patient_id(medication_administration_bundle, patient_id)
    def _include_med(med):
        med_date = pull_attr(med, 'effectivePeriod.start OR effectiveDateTime')
        med_date = datetime.date.fromisoformat(med_date[:10])
        return med_date > encounter_date
    meds = [m for m in meds if _include_med(m)]
    data['medication_administration'] = meds
    print(len(meds))

Patient/e4c9f85f8b2b9a85b32f7d9a67ea1046 2014-03-10
13
Patient/00d7dde9ae58163184c3836f01deff61 2013-08-16
149
Patient/ceba63b6dcbda783668cf3efeea1d3dd 2013-12-23
187
Patient/f7f2e775f7ae3f7a095146cb4deaa497 2012-08-05
25
Patient/ff7c22942a1e16167f1b9c44f12aae05 2014-03-26
165
Patient/6863ac983b0b55455da78f1fdd1288ff 2012-11-28
35


we have 6 patients that meet all inclusion criteria except for having hospitalization records (as part of an encounter)

In [ ]:
# patient_list

In [ ]:
# for patient_id in patient_ids:
#     encounters = extract_resources_by_patient_id(encounter_bundle, patient_id)
#     print(patient_id, len(encounters))
#     for encounter in encounters:
#         print(pull_attr(encounter, 'period'), pull_attr(encounter, 'reasonCode.coding.code'))

In [ ]:
resource = medication_administration_bundle['entry'][0]['resource']
pull_attr(resource, 'effectivePeriod.start OR effectiveDateTime')

'2020-03-13T23:04:26+00:00'

In [ ]:
# for e in medication_administration_bundle['entry']:
#     if pull_attr(e, 'resource.effectiveDateTime') is not None:
#         print('effectiveDateTime')
#     if pull_attr(e, 'resource.effectivePeriod') is not None:
#         print('effectivePeriod')

In [ ]:
# client.get_as_raw_json('MedicationAdministration', {'status': 'completed'})

In [ ]:
for entry in medication_administration_bundle['entry'][10:]:
    print(entry['resource']['effectiveDateTime'])

KeyError: 'effectiveDateTime'

### &uarr; is why we need `pull_attr` &darr;

In [ ]:
for entry in medication_administration_bundle['entry'][10:15]:
    print(pull_attr(entry, 'resource.effectiveDateTime'))

None
None
None
None
None


In [ ]:
entry

{'fullUrl': 'https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io/MedicationAdministration/b4d72d784b9f902a749a6b283f7a262e',
 'resource': {'resourceType': 'MedicationAdministration',
  'id': 'b4d72d784b9f902a749a6b283f7a262e',
  'status': 'completed',
  'medicationCodeableConcept': {'coding': [{'system': 'https://www.nlm.nih.gov/research/umls/rxnorm',
     'code': '1116632',
     'display': 'ticagrelor'}]},
  'subject': {'reference': 'Patient/f7f2e775f7ae3f7a095146cb4deaa497'},
  'effectivePeriod': {'start': '2012-08-12T08:54:00+00:00',
   'end': '2012-08-12T20:54:00+00:00'},
  'meta': {'lastUpdated': '2022-09-17T20:26:23Z', 'versionId': '1'}},
 'search': {'mode': 'match'}}

In [ ]:
reference = extract_references_from_resource(entry['resource'], 'context')
reference

[]

In [ ]:
client.get_by_reference(reference[0])

IndexError: list index out of range

# Apply "after the date of diagnosis of ACS" criteria to medication bundle

Encounter start date is the date of diagnosis of ACS

In [ ]:
mock_encounter_start_date = datetime.date.fromisoformat('1999-09-24')
for entry in medication_administration_bundle['entry']:
    resource = entry['resource']
    print(pull_attr(resource, 'subject.reference'), 
          pull_attr(resource, 'effectiveDateTime'),
          pull_attr(resource, 'context'))
    edt = pull_attr(resource, 'effectiveDateTime')
    if edt is not None:
        edt = datetime.datetime.fromisoformat(edt).date() # Note: we're dropping time part for this comparison
        if edt >= mock_encounter_start_date:
            print('This one would be included', edt, 'is after', mock_encounter_start_date)
        else:
            print('EXCLUDE this one as', edt, 'is before', mock_encounter_start_date)

# Retrieve IPS

```
[base]/Patient/[id]/$retrieveExtendedIPS(?historyPeriod=[# of months])

[base]/Patient/[id]/$summary
```

In [ ]:
client.get_as_raw_json('Patient/1234/$retrieveExtendedIPS')

## non-IPS

In [ ]:
from uuid import uuid4

def timestamp_now():
    return datetime.datetime.utcnow().strftime('%Y-%m-%dT%H:%M:%SZ')

def new_bundle(bundle_type='collection'):
    return dict(resourceType='Bundle', 
                id=str(uuid4()),
                type=bundle_type, 
                timestamp=timestamp_now(),
                entry=[])

def extract_references_from_resource(resource, field_name):
    "Return a list of references extracted from a single resource and field"
    result = []
    if field_name in resource:
        references = resource[field_name]
        if not isinstance(references, list): references = [references]
        for reference in references:
            _reference = reference.get('reference')
            if _reference is None: continue
            if _reference.startswith('#'): continue
            # TODO: check that we have a relative reference or handle other kinds too
            result.append(_reference)
    return result

def get_by_reference(api_base, reference):
    "Return a resource read from a FHIR server by reference, as a list containg a single bundle entry"
    if reference.startswith(api_base):
        reference = reference[len(api_base):].strip('/')
    if reference.startswith('http'):
        print(f'WARNING: Found reference {reference} that does not start with {api_base}')
        return []
    resource_type, id = reference.split('/')
    single_resource = get_as_raw_json(api_base, resource_type, id)
    return [dict(fullUrl = f'{api_base}/{resource_type}/{id}', resource = single_resource)]

def extract_references(bundle, field_names):
    "Return a list of relative references e.g. `['Condition/1ddef4ad-fb76-46d6-9f1d-8ed58b173ee8']`"
    if 'entry' not in bundle: return []
    result = []
    for entry in bundle['entry']:
        resource = entry.get('resource', {})
        for f in field_names:
            result.extend(extract_references_from_resource(resource, f))
    return list(set(result)) # de-duplicate but still return a list

request_headers = {}

def get_as_raw_json(api_base, resource_type, id_or_params=None):
    "GET FHIR resources of `resource_type` in JSON format"
    url = f'{api_base}/{resource_type}'
    params = dict(_format = 'json')
    if isinstance(id_or_params, dict): params = {**params, **id_or_params}
    elif isinstance(id_or_params, str):
        if id_or_params[0] in ['/','?']: raise Exception(f'invalid id_or_params {id_or_params}') # TODO: clean
        url += f'/{id_or_params}'
    response = requests.get(url, params, headers=request_headers)
    print('GET', response.url)
    return response.json()

#export
def get_next_as_raw_json(json_response):
    "GET the next set of results"
    for link in json_response['link']:
        if link['relation'] == 'next':
            url = link['url']
            print('GET',url)
            return requests.get(url, headers=request_headers).json()
        
def create_single_patient_medication_bundle(api_base, patient_id):
    "Return a Bundle containing one Patient and any number of MedicationX resources"
    result = new_bundle()
    references = []
    for resource_type, url_suffix in [
            ['Patient', dict(_id=patient_id)],
            ['AllergyIntolerance', dict(patient=patient_id)],
            ['MedicationRequest', dict(subject=f'Patient/{patient_id}')],
            ['MedicationDispense', dict(subject=f'Patient/{patient_id}')],
            ['MedicationAdministration', dict(subject=f'Patient/{patient_id}')],
            ['MedicationStatement', dict(subject=f'Patient/{patient_id}')]]:
        try:
            single_resource_bundle = get_as_raw_json(api_base, resource_type, url_suffix)
            while single_resource_bundle is not None and single_resource_bundle['total'] > 0:
                result['entry'].extend(single_resource_bundle['entry'])
                # TODO: xxx medicationReference and reasonReference might not be enough
                references.extend(extract_references(single_resource_bundle, ['medicationReference', 'reasonReference']))
                single_resource_bundle = get_next_as_raw_json(single_resource_bundle)
        except Exception as ex:
            print(f'Failed to get {resource_type}, {url_suffix} from {api_base}\n{ex}')
    for reference in set(references):
        try:
            result['entry'].extend(get_by_reference(api_base, reference))
        except Exception as ex:
            print(f'Failed to reference {reference} from {api_base}\n{ex}')
    return result

create_single_patient_medication_bundle(
    'https://fhir.rykpjsvemdtg.workload-prod-fhiraas.isccloud.io',
    'e4c9f85f8b2b9a85b32f7d9a67ea1046')